## Envrionment Setup

- Run `conda env create --name avalon --file=environment.yaml`
- Then switch to `avalon` env by `conda activate avalon`

## Imports

In [1]:
import altair as alt
from pylab import rcParams
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
from sklearn.dummy import DummyClassifier
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import (
    GridSearchCV,
    RandomizedSearchCV,
    cross_validate,
    train_test_split,
)
from sklearn.neighbors import KNeighborsClassifier
from sklearn.pipeline import Pipeline, make_pipeline
from sklearn.svm import SVC
import seaborn as sns
import matplotlib.pyplot as plt
from pandas.plotting import autocorrelation_plot
from statsmodels.tsa.arima.model import ARIMA
from sklearn.metrics import mean_absolute_error, mean_squared_error
import warnings
warnings.filterwarnings("ignore")

## Reading Data

In [3]:
data = pd.read_csv("data/crimedata_csv_AllNeighbourhoods_AllYears.csv", encoding="utf-8")
data.head()

TYPE  YEAR  MONTH  DAY  HOUR  MINUTE  \
0  Break and Enter Commercial  2012     12   14     8      52   
1  Break and Enter Commercial  2019      3    7     2       6   
2  Break and Enter Commercial  2019      8   27     4      12   
3  Break and Enter Commercial  2021      4   26     4      44   
4  Break and Enter Commercial  2014      8    8     5      13   

     HUNDRED_BLOCK NEIGHBOURHOOD            X             Y  
0              NaN      Oakridge  491285.0000  5.453433e+06  
1    10XX SITKA SQ      Fairview  490612.9648  5.457110e+06  
2  10XX ALBERNI ST      West End  491007.7798  5.459174e+06  
3  10XX ALBERNI ST      West End  491007.7798  5.459174e+06  
4  10XX ALBERNI ST      West End  491015.9434  5.459166e+06

In [4]:
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 879861 entries, 0 to 879860
Data columns (total 10 columns):
 #   Column         Non-Null Count   Dtype  
---  ------         --------------   -----  
 0   TYPE           879861 non-null  object 
 1   YEAR           879861 non-null  int64  
 2   MONTH          879861 non-null  int64  
 3   DAY            879861 non-null  int64  
 4   HOUR           879861 non-null  int64  
 5   MINUTE         879861 non-null  int64  
 6   HUNDRED_BLOCK  879849 non-null  object 
 7   NEIGHBOURHOOD  879717 non-null  object 
 8   X              879785 non-null  float64
 9   Y              879785 non-null  float64
dtypes: float64(2), int64(5), object(3)
memory usage: 67.1+ MB


In [5]:
data.describe().T

count          mean           std     min           25%  \
YEAR    879861.0  2.012265e+03  6.183902e+00  2003.0  2.006000e+03   
MONTH   879861.0  6.516683e+00  3.391857e+00     1.0  4.000000e+00   
DAY     879861.0  1.538500e+01  8.757135e+00     1.0  8.000000e+00   
HOUR    879861.0  1.231342e+01  7.463913e+00     0.0  7.000000e+00   
MINUTE  879861.0  1.586139e+01  1.836042e+01     0.0  0.000000e+00   
X       879785.0  4.490074e+05  1.393043e+05     0.0  4.901879e+05   
Y       879785.0  4.977853e+06  1.544127e+06     0.0  5.454211e+06   

                 50%           75%        max  
YEAR    2.012000e+03  2.018000e+03     2023.0  
MONTH   7.000000e+00  9.000000e+00       12.0  
DAY     1.500000e+01  2.300000e+01       31.0  
HOUR    1.400000e+01  1.800000e+01       23.0  
MINUTE  5.000000e+00  3.000000e+01       59.0  
X       4.915699e+05  4.933801e+05   511303.0  
Y       5.457170e+06  5.458718e+06  5512579.0

In [6]:
def missing_zero_values_table(df):
        zero_val = (df == 0.00).astype(int).sum(axis=0)
        mis_val = df.isnull().sum()
        mis_val_percent = 100 * df.isnull().sum() / len(df)
        mz_table = pd.concat([zero_val, mis_val, mis_val_percent], axis=1)
        mz_table = mz_table.rename(
        columns = {0 : 'Zero Values', 1 : 'Missing Values', 2 : '% of Total Values'})
        mz_table['Total Zero Missing Values'] = mz_table['Zero Values'] + mz_table['Missing Values']
        mz_table['% Total Zero Missing Values'] = 100 * mz_table['Total Zero Missing Values'] / len(df)
        mz_table['Data Type'] = df.dtypes
        mz_table = mz_table[
            mz_table.iloc[:,1] != 0].sort_values(
        '% of Total Values', ascending=False).round(1)
        print ("Your selected dataframe has " + str(df.shape[1]) + " columns and " + str(df.shape[0]) + " Rows.\n"      
            "There are " + str(mz_table.shape[0]) +
              " columns that have missing values.")
        return mz_table

missing_zero_values_table(data)

Your selected dataframe has 10 columns and 879861 Rows.
There are 4 columns that have missing values.


Zero Values  Missing Values  % of Total Values  \
NEIGHBOURHOOD            0             144                0.0   
X                    77225              76                0.0   
Y                    77225              76                0.0   
HUNDRED_BLOCK            0              12                0.0   

               Total Zero Missing Values  % Total Zero Missing Values  \
NEIGHBOURHOOD                        144                          0.0   
X                                  77301                          8.8   
Y                                  77301                          8.8   
HUNDRED_BLOCK                         12                          0.0   

              Data Type  
NEIGHBOURHOOD    object  
X               float64  
Y               float64  
HUNDRED_BLOCK    object

In [7]:
data["TYPE"].value_counts()

TYPE
Theft from Vehicle                                        243335
Other Theft                                               219751
Mischief                                                  107268
Offence Against a Person                                   76906
Break and Enter Residential/Other                          72543
Break and Enter Commercial                                 47836
Theft of Vehicle                                           44935
Theft of Bicycle                                           37293
Vehicle Collision or Pedestrian Struck (with Injury)       29319
Vehicle Collision or Pedestrian Struck (with Fatality)       359
Homicide                                                     316
Name: count, dtype: int64

In [8]:
data["NEIGHBOURHOOD"].value_counts()

NEIGHBOURHOOD
Central Business District    237333
West End                      78862
Strathcona                    56667
Mount Pleasant                55435
Fairview                      53853
Grandview-Woodland            49300
Renfrew-Collingwood           47280
Kitsilano                     42859
Kensington-Cedar Cottage      41682
Hastings-Sunrise              30289
Sunset                        29471
Marpole                       22019
Riley Park                    21002
Victoria-Fraserview           17603
Killarney                     16595
Oakridge                      13174
Kerrisdale                    11529
Dunbar-Southlands             11462
West Point Grey                9595
Arbutus Ridge                  9418
South Cambie                   8972
Shaughnessy                    8639
Stanley Park                   5671
Musqueam                       1007
Name: count, dtype: int64

In [9]:
alt.data_transformers.enable('vegafusion')
numeric_cols = ["MONTH", "DAY", "HOUR", "MINUTE"]
numeric_cols_dist = alt.Chart(data).mark_bar().encode(
    alt.X(alt.repeat(), type = "quantitative", bin = alt.Bin(maxbins = 30)),
    y ="count()",
).properties(
        width = 200,
        height = 150
).repeat(
    numeric_cols,
    columns = 1
)

numeric_cols_dist

alt.RepeatChart(...)

In [10]:

categ_cols_dist = alt.Chart(data).mark_bar().encode(
    y = alt.X(alt.repeat(),type= "nominal").sort("x"),
    x =alt.Y("count()"),
).properties(
        width = 500,
        height = 300
).repeat(
     ["TYPE", "NEIGHBOURHOOD"],
    columns = 1
)
categ_cols_dist

alt.RepeatChart(...)

In [11]:
def get_redundant_pairs(df):
    pairs_to_drop = set()
    cols = df.columns
    for i in range(0, df.shape[1]):
        for j in range(0, i+1):
            pairs_to_drop.add((cols[i], cols[j]))
    return pairs_to_drop

def get_top_abs_correlations(df, n=5):
    au_corr = df.corr().abs().unstack()
    labels_to_drop = get_redundant_pairs(df)
    au_corr = au_corr.drop(labels=labels_to_drop).sort_values(ascending=False)
    return au_corr[0:n]

print("Top Absolute Correlations !")
print(get_top_abs_correlations(data.select_dtypes(include=['int32','int64']), 10))

Top Absolute Correlations !
HOUR   MINUTE    0.114717
YEAR   MINUTE    0.056099
       HOUR      0.035971
       MONTH     0.010681
       DAY       0.009736
MONTH  DAY       0.006062
DAY    HOUR      0.004696
MONTH  MINUTE    0.003963
DAY    MINUTE    0.003185
MONTH  HOUR      0.002013
dtype: float64


In [13]:
import folium
from folium.plugins import HeatMap
CBD_district=data.loc[data.NEIGHBOURHOOD=='Central Business District'][['X','Y']]
CBD_district.X.fillna(0, inplace = True)
CBD_district.Y.fillna(0, inplace = True) 

map_1=folium.Map(location=[49.2827, -123.1207], 
                tiles = "OpenStreetMap",
                zoom_start=11)

folium.CircleMarker([49.2727, -123.1307],
                        radius=70,
                        fill_color="#b22222",
                        popup='Other Theft',
                        color='red',
                       ).add_to(map_1)


map_2 = HeatMap(data=CBD_district, radius=20)

map_2.add_to(map_1)
map_1


In [14]:
grouped = data.groupby(['TYPE', 'YEAR', 'MONTH']).size().reset_index(name='Observations')
grouped.head()

TYPE  YEAR  MONTH  Observations
0  Break and Enter Commercial  2003      1           303
1  Break and Enter Commercial  2003      2           254
2  Break and Enter Commercial  2003      3           292
3  Break and Enter Commercial  2003      4           266
4  Break and Enter Commercial  2003      5           290

In [15]:
grouped['YEAR-MONTH'] = pd.to_datetime(grouped[['YEAR', 'MONTH']].assign(DAY=1))
grouped.head()

TYPE  YEAR  MONTH  Observations YEAR-MONTH
0  Break and Enter Commercial  2003      1           303 2003-01-01
1  Break and Enter Commercial  2003      2           254 2003-02-01
2  Break and Enter Commercial  2003      3           292 2003-03-01
3  Break and Enter Commercial  2003      4           266 2003-04-01
4  Break and Enter Commercial  2003      5           290 2003-05-01

In [17]:
grouped = grouped[~((grouped['YEAR'] == 2023) & (grouped['MONTH'] == 11))]
grouped.head()

TYPE  YEAR  MONTH  Observations YEAR-MONTH
0  Break and Enter Commercial  2003      1           303 2003-01-01
1  Break and Enter Commercial  2003      2           254 2003-02-01
2  Break and Enter Commercial  2003      3           292 2003-03-01
3  Break and Enter Commercial  2003      4           266 2003-04-01
4  Break and Enter Commercial  2003      5           290 2003-05-01

In [18]:
theft_from_vehicle = grouped[grouped['TYPE']=='Theft from Vehicle']
theft_from_vehicle.head()

TYPE  YEAR  MONTH  Observations YEAR-MONTH
1433  Theft from Vehicle  2003      1          1438 2003-01-01
1434  Theft from Vehicle  2003      2          1102 2003-02-01
1435  Theft from Vehicle  2003      3          1251 2003-03-01
1436  Theft from Vehicle  2003      4          1528 2003-04-01
1437  Theft from Vehicle  2003      5          1873 2003-05-01

In [19]:
theft_from_vehicle.info()

<class 'pandas.core.frame.DataFrame'>
Index: 250 entries, 1433 to 1682
Data columns (total 5 columns):
 #   Column        Non-Null Count  Dtype         
---  ------        --------------  -----         
 0   TYPE          250 non-null    object        
 1   YEAR          250 non-null    int64         
 2   MONTH         250 non-null    int64         
 3   Observations  250 non-null    int64         
 4   YEAR-MONTH    250 non-null    datetime64[ns]
dtypes: datetime64[ns](1), int64(3), object(1)
memory usage: 11.7+ KB
